#Setup

In [ ]:
!pip uninstall numpy -y
!pip install numpy==1.22.4

Found existing installation: numpy 1.26.4
Uninstalling numpy-1.26.4:
  Successfully uninstalled numpy-1.26.4
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.8/16.8 MB 20.0 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
albucore 0.0.13 requires numpy<2,>=1.24.4, but you have numpy 1.22.4 which is incompatible.
albumentations 1.4.14 requires numpy>=1.24.4, but you have numpy 1.22.4 which is incompatible.
arviz 0.18.0 requires numpy<2.0,>=1.23.0, but you have numpy 1.22.4 which is incompatible.
astropy 6.1.2 requires numpy>=1.23, but you have numpy 1.22.4 which is incompatible.
chex 0.1.86 requires numpy>=1.24.1, but you have numpy 1.22.4 which is incompatible.
cudf-cu12 24.4.1 requires numpy<2.0a0,>=1.23, but you have numpy 1.22.4 which is incompatible.
numexpr 2.10.1 requires numpy>=1.23.0, but you have numpy 1.22.4 which is incompatible.
pandas

In [ ]:
!pip uninstall pandas -y
!pip install pandas==1.4.0

Found existing installation: pandas 2.1.4
Uninstalling pandas-2.1.4:
  Successfully uninstalled pandas-2.1.4
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 11.7/11.7 MB 47.9 MB/s eta 0:00:00
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
arviz 0.18.0 requires numpy<2.0,>=1.23.0, but you have numpy 1.22.4 which is incompatible.
arviz 0.18.0 requires pandas>=1.5.0, but you have pandas 1.4.0 which is incompatible.
bigframes 1.15.0 requires pandas>=1.5.0, but you have pandas 1.4.0 which is incompatible.
cudf-cu12 24.4.1 requires numpy<2.0a0,>=1.23, but you have numpy 1.22.4 which is incompatible.
cudf-cu12 24.4.1 requires pandas<2.2.2dev0,>=2.0, but you have pandas 1.4.0 which is incompatible.
google-colab 1.0.0 requires pandas==2.1.4, but you have pandas 1.4.0 which is incompatible.
plotnine 0.12.4 requires numpy>=1.23.0, but you have numpy 1.22.4 which is incompati

In [ ]:
!pip install optuna

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 362.8/362.8 kB 5.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 233.0/233.0 kB 17.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 78.6/78.6 kB 6.5 MB/s eta 0:00:00


In [ ]:
import csv
import pandas as pd
import scipy.sparse as sps
import numpy as np
import os
from scipy import sparse
import matplotlib.pyplot as pyplot
import traceback
import pickle
import optuna
import time

In [ ]:
from google.colab import drive
drive.flush_and_unmount()
drive.mount('/content/drive', force_remount=True)
import sys
sys.path.append('/content/drive/MyDrive/RSResources')

Drive not mounted, so nothing to flush and unmount.
Mounted at /content/drive


In [ ]:
# Setup path del file di training
data_path = "/content/drive/MyDrive/RSResources/input_files/"
data_file_name = data_path + "data_train.csv"

# Setup lettura file di Train in CSV e creazione URM dataframe
URM_all_dataframe = pd.read_csv(filepath_or_buffer=data_file_name,
                                sep=",",
                                dtype={0:int, 1:int}, # UserId = int , ItemID = int
                                engine='python')

URM_all_dataframe.columns = ["UserID", "ItemID"]
URM_all_dataframe["data"] = 1.0

URM_all_dataframe.head()

#Analisi dei dati
"""
Number of items	 22222, Number of users	 12638
Max ID items	 22347, Max Id users	 13024
"""
#Rimuovere degli indici vuoti, con una mappatura."

mapped_id, original_id = pd.factorize(URM_all_dataframe["UserID"].unique())
user_original_ID_to_index = pd.Series(mapped_id, index=original_id)

mapped_id, original_id = pd.factorize(URM_all_dataframe["ItemID"].unique())
item_original_ID_to_index = pd.Series(mapped_id, index=original_id)

#Sostituiamo gli Id con quelli mappati URM

URM_all_dataframe["UserID"] = URM_all_dataframe["UserID"].map(user_original_ID_to_index)
URM_all_dataframe["ItemID"] = URM_all_dataframe["ItemID"].map(item_original_ID_to_index)


#Analisi dei dati Mappati e rimossi gli indici unici
"""
Number of items	 22222, Number of users	 12638
Max ID items	 22221, Max Id users	 12637
Average interactions per user 37.88
Average interactions per item 21.54

Sparsity 99.83 %
"""
#------------------------------------------------------------------------------------------------------------
                                        #Inizio Analisi Dati
#------------------------------------------------------------------------------------------------------------

#Costruzione Sparse Matrix (COO matrix ) import scipy.sparse, COO constructor expects (data, (row, column)

#MATRIX
URM_all = sps.coo_matrix((URM_all_dataframe["data"].values,(URM_all_dataframe["UserID"].values, URM_all_dataframe["ItemID"].values)))

In [ ]:
URM_all_dataframe.head(10)

UserID  ItemID  data
0       0       0   1.0
1       0       1   1.0
2       0       2   1.0
3       1       3   1.0
4       2       4   1.0
5       2       5   1.0
6       2       6   1.0
7       2       7   1.0
8       2       8   1.0
9       2       9   1.0

In [ ]:
from Data_manager.split_functions.split_train_validation_random_holdout import split_train_in_two_percentage_global_sample
from Evaluation.Evaluator import EvaluatorHoldout

In [ ]:
URM_train_validation, URM_test = split_train_in_two_percentage_global_sample(URM_all, train_percentage = 0.8)
URM_train, URM_validation = split_train_in_two_percentage_global_sample(URM_train_validation, train_percentage = 0.8)

In [ ]:
evaluator_validation = EvaluatorHoldout(URM_validation, cutoff_list=[10])
evaluator_test = EvaluatorHoldout(URM_test, cutoff_list=[10])

EvaluatorHoldout: Ignoring 3 (37.5%) Users that have less than 1 test interactions
EvaluatorHoldout: Ignoring 2 (25.0%) Users that have less than 1 test interactions


# IALSRecommeder

In [ ]:
from Recommenders.MatrixFactorization.IALSRecommender import IALSRecommender
import time
import pickle

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["epochs"] = optuna_trial.user_attrs["epochs"]
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_ials(optuna_trial):

    # Earlystopping hyperparameters available in the framework
    full_hyperp = {"validation_every_n": 5,
                   "stop_on_validation": True,
                   "evaluator_object": evaluator_validation,
                   "lower_validations_allowed": 5,   # Higher values will result in a more "patient" earlystopping
                   "validation_metric": "MAP",

                   # MAX number of epochs (usually 500)
                   "epochs": 500,
                  }

    confidence_scaling = optuna_trial.suggest_categorical("confidence_scaling", ["linear", "log"])
    if confidence_scaling == "log":
      full_hyperp["epsilon"]= optuna_trial.suggest_float("epsilon", 1e-3, 1e-0, log=True)

    start_time = time.time()
    recommender_instance = IALSRecommender(URM_train)
    recommender_instance.fit(num_factors = optuna_trial.suggest_int("num_factors", 1, 200),
                             confidence_scaling = confidence_scaling,
                             reg = optuna_trial.suggest_float("reg", 1e-4, 1e-1, log=True),
                             alpha = optuna_trial.suggest_float("alpha", 1e-3, 1e-0, log=True),
                             init_mean = optuna_trial.suggest_float("init_mean", 1e-1, 1e+1),
                             init_std = optuna_trial.suggest_float("init_std", 1e-1, 1e+1),
                             ** full_hyperp)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    epochs = recommender_instance.get_early_stopping_final_epochs_dict()["epochs"]
    optuna_trial.set_user_attr("epochs", epochs)
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_ials,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-09-02 10:07:12,618] A new study created in memory with name: no-name-e749611f-09c2-49a2-802a-fccc4b47944f


IALSRecommender: URM Detected 1 (12.5%) users with no interactions.
IALSRecommender: URM Detected 16 (27.6%) items with no interactions.
IALSRecommender: Epoch 1 of 500. Elapsed time 0.06 sec
IALSRecommender: Epoch 2 of 500. Elapsed time 0.14 sec
IALSRecommender: Epoch 3 of 500. Elapsed time 0.21 sec
IALSRecommender: Epoch 4 of 500. Elapsed time 0.28 sec
IALSRecommender: Validation begins...
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 854
IALSRecommender: CUTOFF: 10 - PRECISION: 0.0200000, PRECISION_RECALL_MIN_DEN: 0.2000000, RECALL: 0.2000000, MAP: 0.0040000, MAP_MIN_DEN: 0.0400000, MRR: 0.0400000, NDCG: 0.0773706, F1: 0.0363636, HIT_RATE: 0.2000000, ARHR_ALL_HITS: 0.0400000, NOVELTY: 0.2288845, AVERAGE_POPULARITY: 0.1925926, DIVERSITY_MEAN_INTER_LIST: 1.0700000, DIVERSITY_HERFINDAHL: 0.9375000, COVERAGE_ITEM: 0.3275862, COVERAGE_ITEM_HIT: 0.0172414, ITEMS_IN_GT: 0.2068966, COVERAGE_USER: 0.5000000, COVERAGE_USER_HIT: 0.1250000, USERS_IN_GT: 0.6250000, DIVERS

[I 2024-09-02 10:07:15,090] Trial 0 finished with value: 0.004 and parameters: {'confidence_scaling': 'log', 'epsilon': 0.03987101355845867, 'num_factors': 157, 'reg': 0.0003209354897299624, 'alpha': 0.00935242326442508, 'init_mean': 3.527277097596506, 'init_std': 8.923410244214622}. Best is trial 0 with value: 0.004.


IALSRecommender: URM Detected 1 (12.5%) users with no interactions.
IALSRecommender: URM Detected 16 (27.6%) items with no interactions.
IALSRecommender: Epoch 1 of 500. Elapsed time 0.08 sec


<ipython-input-15-977b1e347ca3>:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-09-02 10:08:35,079] Trial 48 finished with value: 0.026500000000000003 and parameters: {'confidence_scaling': 'log', 'epsilon': 0.3576871095516475, 'num_factors': 62, 'reg': 0.004873827570471057, 'alpha': 0.056124490306186575, 'init_mean': 2.4508855677809196, 'init_std': 3.1609856863677646}. Best is trial 13 with value: 0.098.


IALSRecommender: URM Detected 1 (12.5%) users with no interactions.
IALSRecommender: URM Detected 16 (27.6%) items with no interactions.
IALSRecommender: Epoch 1 of 500. Elapsed time 0.03 sec


<ipython-input-15-977b1e347ca3>:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


IALSRecommender: Epoch 2 of 500. Elapsed time 0.08 sec
IALSRecommender: Epoch 3 of 500. Elapsed time 0.14 sec
IALSRecommender: Epoch 4 of 500. Elapsed time 0.18 sec
IALSRecommender: Validation begins...
EvaluatorHoldout: Processed 5 (100.0%) in 0.02 sec. Users per second: 318
IALSRecommender: CUTOFF: 10 - PRECISION: 0.1000000, PRECISION_RECALL_MIN_DEN: 0.4166667, RECALL: 0.4166667, MAP: 0.0463333, MAP_MIN_DEN: 0.1561111, MRR: 0.2833333, NDCG: 0.2556586, F1: 0.1612903, HIT_RATE: 0.6000000, ARHR_ALL_HITS: 0.3566667, NOVELTY: 0.3326890, AVERAGE_POPULARITY: 0.1533333, DIVERSITY_MEAN_INTER_LIST: 0.7500000, DIVERSITY_HERFINDAHL: 0.9600000, COVERAGE_ITEM: 0.5517241, COVERAGE_ITEM_HIT: 0.0862069, ITEMS_IN_GT: 0.2068966, COVERAGE_USER: 0.6250000, COVERAGE_USER_HIT: 0.3750000, USERS_IN_GT: 0.6250000, DIVERSITY_GINI: 0.4257627, SHANNON_ENTROPY: 4.8287584, RATIO_DIVERSITY_HERFINDAHL: 0.9867123, RATIO_DIVERSITY_GINI: 0.6653405, RATIO_SHANNON_ENTROPY: 0.9087564, RATIO_AVERAGE_POPULARITY: 0.3475211, 

[I 2024-09-02 10:08:36,981] Trial 49 finished with value: 0.04633333333333333 and parameters: {'confidence_scaling': 'log', 'epsilon': 0.09139253476754475, 'num_factors': 46, 'reg': 0.008547598223735062, 'alpha': 0.0946362747386562, 'init_mean': 3.701607162106108, 'init_std': 2.475321599572858}. Best is trial 13 with value: 0.098.
<ipython-input-15-977b1e347ca3>:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'confidence_scaling': 'log',
 'epsilon': 0.56367792465005,
 'num_factors': 71,
 'reg': 0.07867780737107673,
 'alpha': 0.22925382418678034,
 'init_mean': 2.1444142558485892,
 'init_std': 5.311288552502352}

In [ ]:
from Recommenders.MatrixFactorization.IALSRecommender import IALSRecommender
IALSRecommender_hyp = IALSRecommender(URM_train + URM_validation)
IALSRecommender_hyp.fit(**optuna_study.best_trial.params)

result_df, _ = evaluator_test.evaluateRecommender(IALSRecommender_hyp)
result_df

IALSRecommender: URM Detected 8 (13.8%) items with no interactions.
IALSRecommender: Epoch 1 of 300. Elapsed time 0.02 sec
IALSRecommender: Epoch 2 of 300. Elapsed time 0.04 sec
IALSRecommender: Epoch 3 of 300. Elapsed time 0.06 sec
IALSRecommender: Epoch 4 of 300. Elapsed time 0.08 sec
IALSRecommender: Epoch 5 of 300. Elapsed time 0.11 sec
IALSRecommender: Epoch 6 of 300. Elapsed time 0.13 sec
IALSRecommender: Epoch 7 of 300. Elapsed time 0.15 sec
IALSRecommender: Epoch 8 of 300. Elapsed time 0.17 sec
IALSRecommender: Epoch 9 of 300. Elapsed time 0.19 sec
IALSRecommender: Epoch 10 of 300. Elapsed time 0.22 sec
IALSRecommender: Epoch 11 of 300. Elapsed time 0.24 sec
IALSRecommender: Epoch 12 of 300. Elapsed time 0.27 sec
IALSRecommender: Epoch 13 of 300. Elapsed time 0.29 sec
IALSRecommender: Epoch 14 of 300. Elapsed time 0.31 sec
IALSRecommender: Epoch 15 of 300. Elapsed time 0.33 sec
IALSRecommender: Epoch 16 of 300. Elapsed time 0.36 sec
IALSRecommender: Epoch 17 of 300. Elapsed tim

PRECISION PRECISION_RECALL_MIN_DEN    RECALL     MAP MAP_MIN_DEN  \
cutoff                                                                    
10          0.05                 0.388889  0.388889  0.0125    0.087963   

          MRR      NDCG        F1 HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                    ...                 
10      0.125  0.170254  0.088608      0.5         0.125  ...          0.75   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10                 0.375        0.75       0.549718        5.160976   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                       0.993245             0.743213              0.928616   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                     0.842879      1.350006  

[1 rows x 27 columns]

# SLIMBPRRecommender

In [ ]:
from Recommenders.SLIM.Cython.SLIM_BPR_Cython import SLIM_BPR_Cython

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["epochs"] = optuna_trial.user_attrs["epochs"]
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_slimbpr(optuna_trial):

    # Earlystopping hyperparameters available in the framework
    full_hyperp = {"validation_every_n": 5,
                   "stop_on_validation": True,
                   "evaluator_object": evaluator_validation,
                   "lower_validations_allowed": 5,   # Higher values will result in a more "patient" earlystopping
                   "validation_metric": "MAP",

                   # MAX number of epochs (usually 500)
                   "epochs": 500,
                  }

    start_time = time.time()
    recommender_instance = SLIM_BPR_Cython(URM_train)
    recommender_instance.fit(symmetric = optuna_trial.suggest_categorical("symmetric", [True, False]),
                             allow_train_with_sparse_weights = optuna_trial.suggest_categorical("allow_train_with_sparse_weights", [True, False]),
                             topK = optuna_trial.suggest_int("topK", 5, 1000, log=True),
                             random_seed = optuna_trial.suggest_int("random_seed", 0, 99, log=False),
                             learning_rate = optuna_trial.suggest_float("learning_rate", 1e-6, 1e-3, log=True),
                             lambda_i = optuna_trial.suggest_float("lambda_i", 1e-4, 1e1, log=True),
                             lambda_j = optuna_trial.suggest_float("lambda_j", 1e-4, 1e1, log=True),
                             sgd_mode = optuna_trial.suggest_categorical("sgd_mode", ["adagrad", "rmsprop", "adam", "sgd"]),
                             gamma = optuna_trial.suggest_float("gamma", 1e-3, 1e1, log=True),
                             beta_1 = optuna_trial.suggest_float("beta_1", 1e-3, 1e1, log=True),
                             beta_2 = optuna_trial.suggest_float("beta_2", 1e-3, 1e1, log=True),
                             ** full_hyperp)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    epochs = recommender_instance.get_early_stopping_final_epochs_dict()["epochs"]
    optuna_trial.set_user_attr("epochs", epochs)
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_slimbpr,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-09-02 10:09:11,807] A new study created in memory with name: no-name-37c3c441-8d67-4443-b359-45e06a031db0


SLIM_BPR_Recommender: URM Detected 1 (12.5%) users with no interactions.
SLIM_BPR_Recommender: URM Detected 16 (27.6%) items with no interactions.
SLIM_BPR_Recommender: Automatic selection of fastest train mode. Available RAM is 11483.00 MB (88.48%) of 12978.00 MB, required is 0.01 MB. Using dense matrix.
Processed 8 (100.0%) in 0.31 sec. BPR loss is NAN. Sample per second: 26
SLIM_BPR_Recommender: Epoch 1 of 500. Elapsed time 0.00 sec
Processed 8 (100.0%) in 0.31 sec. BPR loss is NAN. Sample per second: 25
SLIM_BPR_Recommender: Epoch 2 of 500. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.32 sec. BPR loss is NAN. Sample per second: 25
SLIM_BPR_Recommender: Epoch 3 of 500. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.32 sec. BPR loss is NAN. Sample per second: 25
SLIM_BPR_Recommender: Epoch 4 of 500. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.33 sec. BPR loss is NAN. Sample per second: 25
SLIM_BPR_Recommender: Validation begins...
EvaluatorHoldout: Processed 5 (100.0%) in 0.0

[I 2024-09-02 10:09:13,882] Trial 0 finished with value: 0.029238095238095237 and parameters: {'symmetric': True, 'allow_train_with_sparse_weights': False, 'topK': 35, 'random_seed': 78, 'learning_rate': 0.0001056436240503938, 'lambda_i': 0.03529762183041103, 'lambda_j': 0.002405868501803462, 'sgd_mode': 'rmsprop', 'gamma': 3.492174213433857, 'beta_1': 0.5828330500487711, 'beta_2': 0.02673840129322625}. Best is trial 0 with value: 0.029238095238095237.


Deallocating Cython objects
SLIM_BPR_Recommender: URM Detected 1 (12.5%) users with no interactions.
SLIM_BPR_Recommender: URM Detected 16 (27.6%) items with no interactions.
SLIM_BPR_Recommender: Automatic selection of fastest train mode. Available RAM is 11484.00 MB (88.49%) of 12978.00 MB, required is 0.03 MB. Using dense matrix.
Processed 8 (100.0%) in 0.93 sec. BPR loss is 9.60E-11. Sample per second: 9


<ipython-input-19-ac780b8aed2f>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

Deallocating Cython objects
SLIM_BPR_Recommender: URM Detected 1 (12.5%) users with no interactions.
SLIM_BPR_Recommender: URM Detected 16 (27.6%) items with no interactions.
SLIM_BPR_Recommender: Automatic selection of fastest train mode. Available RAM is 11447.00 MB (88.20%) of 12978.00 MB, required is 0.03 MB. Using dense matrix.
Processed 8 (100.0%) in 0.51 sec. BPR loss is 4.11E-06. Sample per second: 16


<ipython-input-19-ac780b8aed2f>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


SLIM_BPR_Recommender: Epoch 1 of 500. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.52 sec. BPR loss is 2.27E-04. Sample per second: 15
SLIM_BPR_Recommender: Epoch 2 of 500. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.53 sec. BPR loss is 7.79E-01. Sample per second: 15
SLIM_BPR_Recommender: Epoch 3 of 500. Elapsed time 0.02 sec
Processed 8 (100.0%) in 0.53 sec. BPR loss is 1.33E+00. Sample per second: 15
SLIM_BPR_Recommender: Epoch 4 of 500. Elapsed time 0.02 sec
Processed 8 (100.0%) in 0.53 sec. BPR loss is 6.30E+02. Sample per second: 15
SLIM_BPR_Recommender: Validation begins...
EvaluatorHoldout: Processed 5 (100.0%) in 0.03 sec. Users per second: 178
SLIM_BPR_Recommender: CUTOFF: 10 - PRECISION: 0.0400000, PRECISION_RECALL_MIN_DEN: 0.1000000, RECALL: 0.1000000, MAP: 0.0116667, MAP_MIN_DEN: 0.0291667, MRR: 0.0666667, NDCG: 0.0636682, F1: 0.0571429, HIT_RATE: 0.2000000, ARHR_ALL_HITS: 0.0916667, NOVELTY: 0.6285704, AVERAGE_POPULARITY: 0.2400000, DIVERSITY_MEAN_INTER_LIST: 0.750

[I 2024-09-02 10:09:59,223] Trial 49 finished with value: 0.002 and parameters: {'symmetric': False, 'allow_train_with_sparse_weights': True, 'topK': 37, 'random_seed': 88, 'learning_rate': 0.0002855485516287555, 'lambda_i': 0.0020606622633168193, 'lambda_j': 4.90561775741646, 'sgd_mode': 'adam', 'gamma': 0.025334542471738126, 'beta_1': 0.022767001792083227, 'beta_2': 2.0594952440725534}. Best is trial 34 with value: 0.2.


<ipython-input-19-ac780b8aed2f>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'symmetric': True,
 'allow_train_with_sparse_weights': True,
 'topK': 209,
 'random_seed': 76,
 'learning_rate': 1.8003042092752915e-06,
 'lambda_i': 3.3855771148175933,
 'lambda_j': 0.001577267842002536,
 'sgd_mode': 'rmsprop',
 'gamma': 4.09303945426835,
 'beta_1': 0.22192080611592693,
 'beta_2': 8.524907215761356}

In [ ]:
from Recommenders.SLIM.Cython.SLIM_BPR_Cython import SLIM_BPR_Cython

slim_bpr_hyp = SLIM_BPR_Cython(URM_train + URM_validation)
slim_bpr_hyp.fit(**optuna_study.best_trial.params)

result_df, _ = evaluator_test.evaluateRecommender(slim_bpr_hyp)
result_df

SLIM_BPR_Recommender: URM Detected 8 (13.8%) items with no interactions.
SLIM_BPR_Recommender: Automatic selection of fastest train mode. Available RAM is 11442.00 MB (88.16%) of 12978.00 MB, required is 0.01 MB. Using dense matrix.
Processed 8 (100.0%) in 0.80 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 1 of 300. Elapsed time 0.00 sec
Processed 8 (100.0%) in 0.80 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 2 of 300. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.81 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 3 of 300. Elapsed time 0.01 sec
Processed 8 (100.0%) in 0.81 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 4 of 300. Elapsed time 0.02 sec
Processed 8 (100.0%) in 0.82 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 5 of 300. Elapsed time 0.02 sec
Processed 8 (100.0%) in 0.82 sec. BPR loss is NAN. Sample per second: 10
SLIM_BPR_Recommender: Epoch 6

PRECISION PRECISION_RECALL_MIN_DEN RECALL  MAP MAP_MIN_DEN  MRR NDCG  \
cutoff                                                                        
10           0.0                      0.0    0.0  0.0         0.0  0.0  0.0   

         F1 HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER COVERAGE_USER_HIT  \
cutoff                              ...                                   
10      0.0      0.0           0.0  ...         0.375               0.0   

       USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL  \
cutoff                                                                         
10            0.75       0.133475        3.030639                    0.88746   

       RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY  \
cutoff                                                                       
10                 0.180456              0.545304                 0.418553   

       RATIO_NOVELTY  
cutoff                
10          0.338077  

[1 rows x 27 columns]

# ElasticNetRecommender

In [ ]:
from Recommenders.SLIM.SLIMElasticNetRecommender import SLIMElasticNetRecommender

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_elasticnet(optuna_trial):

    start_time = time.time()
    recommender_instance = SLIMElasticNetRecommender(URM_train)
    recommender_instance.fit(positive_only = optuna_trial.suggest_categorical("positive_only", [True, False]),
                             topK = optuna_trial.suggest_int("topK", 5, 1000, log=True),
                             l1_ratio = optuna_trial.suggest_float("l1_ratio", 0.001, 1.000, log=True),
                             alpha = optuna_trial.suggest_float("alpha", 1e-4, 1e-1, log=True))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_elasticnet,
                      callbacks=[save_results],
                      n_trials = 30)

[I 2024-09-02 10:11:01,521] A new study created in memory with name: no-name-6fc189db-56c8-46eb-ac09-94602072300a


SLIMElasticNetRecommender: URM Detected 1 (12.5%) users with no interactions.
SLIMElasticNetRecommender: URM Detected 16 (27.6%) items with no interactions.
SLIMElasticNetRecommender: Processed 58 (100.0%) in 0.14 sec. Items per second: 401.99
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 677


[I 2024-09-02 10:11:01,696] Trial 0 finished with value: 0.0 and parameters: {'positive_only': True, 'topK': 12, 'l1_ratio': 0.7252738995616528, 'alpha': 0.0020364761392740525}. Best is trial 0 with value: 0.0.


..........Calling pickle to save current results..............


<ipython-input-23-086ffc8f72e9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-09-02 10:11:06,981] Trial 28 finished with value: 0.0 and parameters: {'positive_only': True, 'topK': 5, 'l1_ratio': 0.09344824027015607, 'alpha': 0.008144365753405082}. Best is trial 11 with value: 0.002857142857142857.
<ipython-input-23-086ffc8f72e9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


..........Calling pickle to save current results..............
SLIMElasticNetRecommender: URM Detected 1 (12.5%) users with no interactions.
SLIMElasticNetRecommender: URM Detected 16 (27.6%) items with no interactions.
SLIMElasticNetRecommender: Processed 58 (100.0%) in 0.09 sec. Items per second: 631.77
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 994


[I 2024-09-02 10:11:07,142] Trial 29 finished with value: 0.0 and parameters: {'positive_only': False, 'topK': 16, 'l1_ratio': 0.0015010775175840901, 'alpha': 0.040996718568786394}. Best is trial 11 with value: 0.002857142857142857.


..........Calling pickle to save current results..............


<ipython-input-23-086ffc8f72e9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'positive_only': False,
 'topK': 5,
 'l1_ratio': 0.12361457416704681,
 'alpha': 0.0008811086271662717}

In [ ]:
from Recommenders.SLIM.SLIMElasticNetRecommender import SLIMElasticNetRecommender

elastic_net = SLIMElasticNetRecommender(URM_train + URM_validation)
elastic_net.fit(
    positive_only = optuna_study.best_trial.params["positive_only"],
    topK = optuna_study.best_trial.params["topK"],
    alpha = optuna_study.best_trial.params["alpha"],
    l1_ratio = optuna_study.best_trial.params["l1_ratio"]
    )

result_df, _ = evaluator_test.evaluateRecommender(elastic_net)
result_df

SLIMElasticNetRecommender: URM Detected 8 (13.8%) items with no interactions.
SLIMElasticNetRecommender: Processed 58 (100.0%) in 0.09 sec. Items per second: 615.27
EvaluatorHoldout: Processed 6 (100.0%) in 0.01 sec. Users per second: 1140


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10          0.05                 0.263889  0.263889  0.008631    0.054812   

            MRR      NDCG        F1 HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                      ...                 
10      0.08631  0.118376  0.084071      0.5       0.08631  ...          0.75   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10                 0.375        0.75       0.519209         5.10248   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                       0.991539             0.701966              0.918091   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                      0.80824      1.280031  

[1 rows x 27 columns]

# ItemKNNCFRecommender

In [ ]:
from Recommenders.KNN.ItemKNNCFRecommender import ItemKNNCFRecommender
def objective_function_KNN_similarities(optuna_trial):

    recommender_instance = ItemKNNCFRecommender(URM_train)
    similarity = optuna_trial.suggest_categorical("similarity", ['cosine', 'dice', 'jaccard', 'asymmetric', 'tversky', 'euclidean'])

    full_hyperp = {"similarity": similarity,
                   "topK": optuna_trial.suggest_int("topK", 5, 1000),
                   "shrink": optuna_trial.suggest_int("shrink", 0, 1000),
                   "normalize": optuna_trial.suggest_categorical("normalize", [True, False])
                  }

    if similarity == "asymmetric":
        full_hyperp["asymmetric_alpha"] = optuna_trial.suggest_float("asymmetric_alpha", 0, 2, log=False)
    elif similarity == "tversky":
        full_hyperp["tversky_alpha"] = optuna_trial.suggest_float("tversky_alpha", 0, 2, log=False)
        full_hyperp["tversky_beta"] = optuna_trial.suggest_float("tversky_beta", 0, 2, log=False)

    elif similarity == "euclidean":
        full_hyperp["normalize_avg_row"] = optuna_trial.suggest_categorical("normalize_avg_row", [True, False])
        full_hyperp["similarity_from_distance_mode"] = optuna_trial.suggest_categorical("similarity_from_distance_mode", ["lin", "log", "exp"])


    recommender_instance.fit(**full_hyperp)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns = ["result"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)
        print("..........Calling pickle to save current results..............")
        pickle.dump(self.results_df, open("/content/drive/MyDrive/RSResources/Training/ItemKNNCF", "wb"))

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_KNN_similarities,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-09-02 10:21:25,649] A new study created in memory with name: no-name-a76d5790-2290-456a-ba6a-79b4121e42aa


ItemKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
ItemKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.
Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 58 (100.0%), 16481.68 column/sec. Elapsed time 0.00 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.00 sec. Users per second: 1173


[I 2024-09-02 10:21:25,680] Trial 0 finished with value: 0.0 and parameters: {'similarity': 'dice', 'topK': 876, 'shrink': 85, 'normalize': False}. Best is trial 0 with value: 0.0.


..........Calling pickle to save current results..............
ItemKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
ItemKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.
Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 58 (100.0%), 15021.28 column/sec. Elapsed time 0.00 sec


<ipython-input-42-6d857b6e65c5>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

..........Calling pickle to save current results..............


<ipython-input-42-6d857b6e65c5>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


ItemKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
ItemKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.
Similarity column 58 (100.0%), 2986.70 column/sec. Elapsed time 0.02 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 553


[I 2024-09-02 10:21:30,433] Trial 49 finished with value: 0.033 and parameters: {'similarity': 'euclidean', 'topK': 557, 'shrink': 130, 'normalize': False, 'normalize_avg_row': True, 'similarity_from_distance_mode': 'log'}. Best is trial 4 with value: 0.033.
<ipython-input-42-6d857b6e65c5>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


..........Calling pickle to save current results..............


In [ ]:
optuna_study.best_trial.params

{'similarity': 'euclidean',
 'topK': 702,
 'shrink': 221,
 'normalize': False,
 'normalize_avg_row': False,
 'similarity_from_distance_mode': 'log'}

In [ ]:
best_recommender_hyperparams = optuna_study.best_trial.params

In [ ]:
from Recommenders.KNN.ItemKNNCFRecommender import ItemKNNCFRecommender
ItemKNNCF_hyp = ItemKNNCFRecommender(URM_train + URM_validation)
ItemKNNCF_hyp.fit(**optuna_study.best_trial.params)
result_df, _ = evaluator_test.evaluateRecommender(ItemKNNCF_hyp)
result_df

ItemKNNCFRecommender: URM Detected 8 (13.8%) items with no interactions.
Similarity column 58 (100.0%), 2076.48 column/sec. Elapsed time 0.03 sec
EvaluatorHoldout: Processed 6 (100.0%) in 0.01 sec. Users per second: 509


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10          0.15                 0.472222  0.472222  0.092679    0.264435   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.527778  0.385136  0.227679  0.666667      0.707606  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10              0.75               0.5        0.75       0.268362   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10            4.192272                   0.957995             0.362822   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.754317                 0.242472      0.462567  

[1 rows x 27 columns]

# UserKNNCFRecommender

In [ ]:
from Recommenders.KNN.UserKNNCFRecommender import UserKNNCFRecommender
def objective_function_KNN_similarities(optuna_trial):

    recommender_instance = UserKNNCFRecommender(URM_train)
    similarity = optuna_trial.suggest_categorical("similarity", ['cosine', 'dice', 'jaccard', 'asymmetric', 'tversky', 'euclidean'])

    full_hyperp = {"similarity": similarity,
                   "topK": optuna_trial.suggest_int("topK", 5, 1000),
                   "shrink": optuna_trial.suggest_int("shrink", 0, 1000),
                   "normalize": optuna_trial.suggest_categorical("normalize", [True, False])
                  }

    if similarity == "asymmetric":
        full_hyperp["asymmetric_alpha"] = optuna_trial.suggest_float("asymmetric_alpha", 0, 2, log=False)

    elif similarity == "tversky":
        full_hyperp["tversky_alpha"] = optuna_trial.suggest_float("tversky_alpha", 0, 2, log=False)
        full_hyperp["tversky_beta"] = optuna_trial.suggest_float("tversky_beta", 0, 2, log=False)

    elif similarity == "euclidean":
        full_hyperp["normalize_avg_row"] = optuna_trial.suggest_categorical("normalize_avg_row", [True, False])
        full_hyperp["similarity_from_distance_mode"] = optuna_trial.suggest_categorical("similarity_from_distance_mode", ["lin", "log", "exp"])


    recommender_instance.fit(**full_hyperp)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns = ["result"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_KNN_similarities,
                      callbacks=[save_results],
                      n_trials = 300)

[I 2024-09-02 10:13:28,807] A new study created in memory with name: no-name-3d529277-20ac-4079-810a-76edb53cbada


UserKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
UserKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.
Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 8 (100.0%), 4946.84 column/sec. Elapsed time 0.00 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.00 sec. Users per second: 1114


[I 2024-09-02 10:13:28,836] Trial 0 finished with value: 0.0 and parameters: {'similarity': 'tversky', 'topK': 932, 'shrink': 847, 'normalize': True, 'tversky_alpha': 0.5596957576119086, 'tversky_beta': 0.06642402656039081}. Best is trial 0 with value: 0.0.


UserKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
UserKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.
Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 8 (100.0%), 5384.21 column/sec. Elapsed time 0.00 sec


<ipython-input-33-650f32a8104f>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-09-02 10:14:10,822] Trial 298 finished with value: 0.0 and parameters: {'similarity': 'dice', 'topK': 579, 'shrink': 872, 'normalize': False}. Best is trial 0 with value: 0.0.


UserKNNCFRecommender: URM Detected 1 (12.5%) users with no interactions.
UserKNNCFRecommender: URM Detected 16 (27.6%) items with no interactions.


<ipython-input-33-650f32a8104f>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 8 (100.0%), 3097.43 column/sec. Elapsed time 0.00 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 768


[I 2024-09-02 10:14:10,944] Trial 299 finished with value: 0.0 and parameters: {'similarity': 'cosine', 'topK': 929, 'shrink': 971, 'normalize': True}. Best is trial 0 with value: 0.0.
<ipython-input-33-650f32a8104f>:10: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'similarity': 'tversky',
 'topK': 932,
 'shrink': 847,
 'normalize': True,
 'tversky_alpha': 0.5596957576119086,
 'tversky_beta': 0.06642402656039081}

In [ ]:
from Recommenders.KNN.UserKNNCFRecommender import UserKNNCFRecommender
UserKNNCF_hyp = UserKNNCFRecommender(URM_train + URM_validation)
UserKNNCF_hyp.fit(**optuna_study.best_trial.params)
result_df, _ = evaluator_test.evaluateRecommender(UserKNNCF_hyp)
result_df

UserKNNCFRecommender: URM Detected 8 (13.8%) items with no interactions.
Unable to load Cython Compute_Similarity, reverting to Python
Similarity column 8 (100.0%), 5124.38 column/sec. Elapsed time 0.00 sec
EvaluatorHoldout: Processed 6 (100.0%) in 0.01 sec. Users per second: 1148


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10          0.05                 0.263889  0.263889  0.022381    0.094841   

            MRR      NDCG        F1 HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                      ...                 
10      0.22381  0.164376  0.084071      0.5       0.22381  ...          0.75   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10                 0.375        0.75       0.472316        4.989898   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                       0.988128             0.638567              0.897834   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                      0.90061      1.330341  

[1 rows x 27 columns]

# # P3BetaRecommender (Not used in the application AI server)

In [ ]:
from Recommenders.GraphBased.RP3betaRecommender import RP3betaRecommender
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_p3beta(optuna_trial):
    start_time = time.time()
    recommender_instance = RP3betaRecommender(URM_train)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 1e-1, 1e+0, log=True),
                             beta = optuna_trial.suggest_float("beta", 1e-1, 1e+0, log=True),
                             topK = optuna_trial.suggest_int("topK", 5, 1000),
                             min_rating = 1,
                             implicit = False,
                             normalize_similarity = True)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_p3beta,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-09-02 09:31:21,224] A new study created in memory with name: no-name-66a47c91-2e96-466b-b38a-13e3a25cadae


RP3betaRecommender: URM Detected 17 (29.3%) items with no interactions.


[W 2024-09-02 09:31:21,246] Trial 0 failed with parameters: {'alpha': 0.21117414474752744, 'beta': 0.741858577426455, 'topK': 63} because of the following error: ValueError('kth(=62) out of bounds (58)').
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/optuna/study/_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
  File "<ipython-input-51-734a6c51de66>", line 20, in objective_function_p3beta
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 1e-1, 1e+0, log=True),
  File "/content/drive/MyDrive/RSResources/Recommenders/GraphBased/RP3betaRecommender.py", line 100, in fit
    relevant_items_partition = np.argpartition(-row_data, self.topK-1, axis=0)[:self.topK]
  File "<__array_function__ internals>", line 180, in argpartition
  File "/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py", line 845, in argpartition
    return _wrapfunc(a, 'argpartition', kth, axis=axis, kind=kind, order=order)
  

ValueError: kth(=62) out of bounds (58)

In [ ]:
optuna_study.best_trial.params

{'alpha': 0.17940241089939363, 'beta': 0.16719315538112617, 'topK': 50}

In [ ]:
from Recommenders.GraphBased.RP3betaRecommender import RP3betaRecommender
P3Beta_hyp = RP3betaRecommender(URM_train + URM_validation)
P3Beta_hyp.fit(**optuna_study.best_trial.params)

result_df, _ = evaluator_test.evaluateRecommender(P3Beta_hyp)
result_df

RP3betaRecommender: URM Detected 217 ( 1.7%) users with no interactions.
RP3betaRecommender: URM Detected 121 ( 0.5%) items with no interactions.
RP3betaRecommender: Similarity column 22222 (100.0%), 3972.74 column/sec. Elapsed time 5.59 sec
EvaluatorHoldout: Processed 10475 (100.0%) in 5.06 sec. Users per second: 2069


PRECISION PRECISION_RECALL_MIN_DEN    RECALL      MAP MAP_MIN_DEN  \
cutoff                                                                     
10       0.09411                  0.16364  0.138127  0.04801    0.081435   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.267137  0.148056  0.111947  0.517422      0.353558  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.428865     0.82885       0.089596   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10           10.681927                   0.998153             0.257382   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.822953                 1.581311      0.298713  

[1 rows x 27 columns]

In [ ]:
P3Beta = RP3betaRecommender(URM_train + URM_validation + URM_test)
P3Beta.fit(alpha = best_hyperparams_graph["alpha"], topK=int(best_hyperparams_graph["topK"]), beta = best_hyperparams_graph["beta"])

RP3betaRecommender: Similarity column 22222 (100.0%), 3534.05 column/sec. Elapsed time 6.29 sec


# P3AlphaRecommender (Not used in the application AI server)

In [ ]:
from Recommenders.GraphBased.P3alphaRecommender import P3alphaRecommender
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_p3alpha(optuna_trial):
    start_time = time.time()
    recommender_instance = P3alphaRecommender(URM_train)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 1e-1, 1e+0, log=True),
                             topK = optuna_trial.suggest_int("topK", 5, 1000),
                             implicit = True,
                             normalize_similarity = True)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_p3alpha,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-09-02 09:32:55,763] A new study created in memory with name: no-name-a088f70e-caab-4f92-a8b4-d8b24e949ef4


P3alphaRecommender: URM Detected 17 (29.3%) items with no interactions.


[W 2024-09-02 09:32:55,778] Trial 0 failed with parameters: {'alpha': 0.23571992075911014, 'topK': 467} because of the following error: ValueError('kth(=466) out of bounds (58)').
Traceback (most recent call last):
  File "/usr/local/lib/python3.10/dist-packages/optuna/study/_optimize.py", line 197, in _run_trial
    value_or_values = func(trial)
  File "<ipython-input-53-679708e90683>", line 20, in objective_function_p3alpha
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 1e-1, 1e+0, log=True),
  File "/content/drive/MyDrive/RSResources/Recommenders/GraphBased/P3alphaRecommender.py", line 91, in fit
    relevant_items_partition = np.argpartition(-row_data, self.topK-1, axis=0)[:self.topK]
  File "<__array_function__ internals>", line 180, in argpartition
  File "/usr/local/lib/python3.10/dist-packages/numpy/core/fromnumeric.py", line 845, in argpartition
    return _wrapfunc(a, 'argpartition', kth, axis=axis, kind=kind, order=order)
  File "/usr/local/lib/pyth

ValueError: kth(=466) out of bounds (58)

In [ ]:
optuna_study.best_trial.params

In [ ]:
from Recommenders.GraphBased.P3alphaRecommender import P3alphaRecommender
P3Alpha_hyp = P3alphaRecommender(URM_train + URM_validation)
P3Alpha_hyp.fit(fit(**optuna_study.best_trial.params))
result_df, _ = evaluator_test.evaluateRecommender(P3Alpha_hyp)
result_df

P3alphaRecommender: URM Detected 217 ( 1.7%) users with no interactions.
P3alphaRecommender: URM Detected 121 ( 0.5%) items with no interactions.
P3alphaRecommender: Similarity column 22222 (100.0%), 3225.67 column/sec. Elapsed time 6.89 sec
EvaluatorHoldout: Processed 10475 (100.0%) in 6.68 sec. Users per second: 1567


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.091093                 0.155782  0.131323  0.046532    0.078494   

            MRR      NDCG       F1  HIT_RATE ARHR_ALL_HITS  ... COVERAGE_USER  \
cutoff                                                      ...                 
10      0.26133  0.143018  0.10757  0.505107      0.344644  ...       0.82885   

       COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI SHANNON_ENTROPY  \
cutoff                                                                
10              0.418658     0.82885        0.06292       10.383282   

       RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI RATIO_SHANNON_ENTROPY  \
cutoff                                                                         
10                       0.998305             0.180748              0.799945   

       RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                         
10                     1.433086      0.295963  

[1 rows x 27 columns]

In [ ]:
P3Alpha = P3alphaRecommender(URM_train + URM_validation + URM_test)
P3Alpha.fit(alpha = best_hyperparams_palpha["alpha"], topK=int(best_hyperparams_palpha["topK"]), implicit=True, normalize_similarity=True)

P3alphaRecommender: Similarity column 22222 (100.0%), 2958.02 column/sec. Elapsed time 7.51 sec


# SLIMMSERecommender (Not used in the application AI server)

In [ ]:
from Recommenders.SLIM.SLIMMSERecommender import SLIMMSERecommender

In [ ]:
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)
        print("..........Calling pickle to save current results..............")
        pickle.dump(self.results_df, open("/content/drive/MyDrive/Prova/Training/SLIMMSE2", "wb"))


def objective_function_slimmse(optuna_trial):
    start_time = time.time()
    recommender_instance = SLIMMSERecommender(URM_train)
    recommender_instance.fit(learning = optuna_trial.suggest_float("learning", 1e-6, 1e-3, log=True),
                             reg_1 = optuna_trial.suggest_float("reg_1", 1e-5, 1e-2, log=True),
                             reg_2 = optuna_trial.suggest_float("reg_2", 1e-5, 1e-2, log=True),
                             epochs = optuna_trial.suggest_int("epochs", 40, 500)
                             )

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    #epochs = recommender_instance.get_early_stopping_final_epochs_dict()["epochs"]
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_slimmse,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-05 11:30:57,525] A new study created in memory with name: no-name-b7457e38-a16e-4ada-b361-74c27592a76d


Recommender_Base_Class: URM Detected 482 ( 3.8%) users with no interactions.
Recommender_Base_Class: URM Detected 340 ( 1.5%) items with no interactions.
Epoch 1 complete in in 9.54 seconds, loss is 9.097E-01. Samples per second 32099.89
Epoch 2 complete in in 1.59 seconds, loss is 7.746E-01. Samples per second 192366.48
Epoch 3 complete in in 1.50 seconds, loss is 6.831E-01. Samples per second 204607.90
Epoch 4 complete in in 1.40 seconds, loss is 6.161E-01. Samples per second 219438.89
Epoch 5 complete in in 1.29 seconds, loss is 5.628E-01. Samples per second 238418.36
Epoch 6 complete in in 1.19 seconds, loss is 5.196E-01. Samples per second 256977.39
Epoch 7 complete in in 1.07 seconds, loss is 4.841E-01. Samples per second 287640.17
Epoch 8 complete in in 1.06 seconds, loss is 4.525E-01. Samples per second 289234.84
Epoch 9 complete in in 1.11 seconds, loss is 4.262E-01. Samples per second 275566.17
Epoch 10 complete in in 1.18 seconds, loss is 4.033E-01. Samples per second 260696

[I 2024-01-05 11:37:23,787] Trial 0 finished with value: 0.01569427837562551 and parameters: {'learning': 0.00046681772549372647, 'reg_1': 0.0032153848477324922, 'reg_2': 0.0005041732113037613, 'epochs': 389}. Best is trial 0 with value: 0.01569427837562551.


..........Calling pickle to save current results..............
Recommender_Base_Class: URM Detected 482 ( 3.8%) users with no interactions.
Recommender_Base_Class: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-7-e41efab30913>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

<ipython-input-7-e41efab30913>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


Epoch 1 complete in in 6.84 seconds, loss is 9.960E-01. Samples per second 44781.51
Epoch 2 complete in in 3.02 seconds, loss is 9.882E-01. Samples per second 101400.34
Epoch 3 complete in in 2.10 seconds, loss is 9.805E-01. Samples per second 145891.39
Epoch 4 complete in in 2.23 seconds, loss is 9.730E-01. Samples per second 137186.07
Epoch 5 complete in in 2.31 seconds, loss is 9.656E-01. Samples per second 132611.39
Epoch 6 complete in in 2.22 seconds, loss is 9.585E-01. Samples per second 137990.05
Epoch 7 complete in in 2.17 seconds, loss is 9.514E-01. Samples per second 141369.28
Epoch 8 complete in in 2.10 seconds, loss is 9.445E-01. Samples per second 145946.07
Epoch 9 complete in in 2.03 seconds, loss is 9.376E-01. Samples per second 151218.59
Epoch 10 complete in in 2.07 seconds, loss is 9.308E-01. Samples per second 148233.16
Epoch 11 complete in in 2.24 seconds, loss is 9.243E-01. Samples per second 136814.90
Epoch 12 complete in in 2.29 seconds, loss is 9.175E-01. Samples

[I 2024-01-05 17:45:13,499] Trial 49 finished with value: 0.022714015259352044 and parameters: {'learning': 1.708490393983062e-05, 'reg_1': 0.00025395260424137845, 'reg_2': 0.0009583713382167398, 'epochs': 472}. Best is trial 43 with value: 0.02273578609070836.


..........Calling pickle to save current results..............


<ipython-input-7-e41efab30913>:13: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'learning': 2.672190484973793e-05,
 'reg_1': 0.0016043095608199854,
 'reg_2': 2.9651907170347154e-05,
 'epochs': 314}

In [ ]:
save_results.results_df

result  train_time (min)  learning     reg_1     reg_2  epochs
0   0.015694          6.194914  0.000467  0.003215  0.000504   389.0
1   0.021532          5.236378  0.000064  0.008853  0.007521   299.0
2   0.020863          6.599894  0.000073  0.001357  0.001578   379.0
3   0.014351          5.883708  0.000844  0.004096  0.000309   339.0
4   0.018246          5.512924  0.000004  0.003830  0.000215   297.0
5   0.014502          2.104691  0.000003  0.000336  0.001272    85.0
6   0.019726          5.601178  0.000008  0.000200  0.000057   229.0
7   0.014621          6.691319  0.000001  0.000164  0.009945   260.0
8   0.016438          7.011126  0.000535  0.000773  0.000719   265.0
9   0.014649          9.992921  0.000611  0.000809  0.001065   424.0
10  0.020326          9.721850  0.000070  0.000023  0.009870   497.0
11  0.022503          3.258844  0.000068  0.009494  0.003700   159.0
12  0.021780          4.667550  0.000021  0.009566  0.003661   164.0
13  0.021019          3.663541  0.000019  0.009703  0.000011   135.0
14  0.020511          5.098572  0.000175  0.000031  0.003141   184.0
15  0.018569          1.994898  0.000022  0.001858  0.003225    65.0
16  0.020445          4.691903  0.000205  0.009062  0.000127   163.0
17  0.017731          3.297550  0.000011  0.000066  0.003486   105.0
18  0.022705          5.905315  0.000036  0.002182  0.002443   207.0
19  0.020540          5.895311  0.000159  0.001919  0.001910   201.0
20  0.019693          1.405418  0.000046  0.000578  0.000045    42.0
21  0.022095          3.804575  0.000031  0.005862  0.004976   126.0
22  0.022479          3.395473  0.000041  0.004726  0.005382   120.0
23  0.020707          6.469933  0.000136  0.002659  0.005558   219.0
24  0.022566          4.157912  0.000043  0.005161  0.001946   138.0
25  0.021884          4.787511  0.000100  0.001153  0.000657   164.0
26  0.018259          8.261818  0.000310  0.002381  0.002097   236.0
27  0.019318          4.906468  0.000012  0.000011  0.000956   145.0
28  0.022722          6.718112  0.000035  0.005391  0.002451   199.0
29  0.022565          6.508349  0.000033  0.005455  0.000449   192.0
30  0.020272          9.922126  0.000007  0.003200  0.002078   302.0
31  0.022727          6.903701  0.000036  0.005665  0.000512   205.0
32  0.022007          7.733376  0.000016  0.006024  0.000423   239.0
33  0.022647          6.360322  0.000048  0.001430  0.000180   186.0
34  0.021317          6.802348  0.000107  0.001317  0.000143   205.0
35  0.022721         10.740257  0.000028  0.000448  0.000227   325.0
36  0.022635         10.634896  0.000029  0.000322  0.000246   328.0
37  0.018811         12.339501  0.000004  0.000477  0.000107   376.0
38  0.022183          9.509004  0.000014  0.003723  0.000082   289.0
39  0.021175         10.919583  0.000008  0.000188  0.000362   338.0
40  0.015359          8.375648  0.000002  0.000106  0.000682   251.0
41  0.022175          8.822306  0.000055  0.000932  0.000265   273.0
42  0.021468          7.109019  0.000093  0.002141  0.000184   213.0
43  0.022736         10.252474  0.000027  0.001604  0.000030   314.0
44  0.022667         12.979742  0.000025  0.003519  0.000018   390.0
45  0.022524         10.147182  0.000033  0.000622  0.000034   320.0
46  0.020841         12.396985  0.000076  0.006536  0.000023   374.0
47  0.022069         11.509656  0.000011  0.000407  0.001276   353.0
48  0.022734         13.343233  0.000020  0.002789  0.000903   419.0
49  0.022714         15.358120  0.000017  0.000254  0.000958   472.0

In [ ]:
slim_result = pickle.load(open("/content/drive/MyDrive/Prova/Training/SLIMMSE2", "rb"))
best_index = slim_result["result"].idxmax()
best_hyperparams_slim = slim_result.loc[best_index].to_dict()

del best_hyperparams_slim["result"]
del best_hyperparams_slim["train_time (min)"]
best_hyperparams_slim

{'learning': 2.672190484973793e-05,
 'reg_1': 0.0016043095608199854,
 'reg_2': 2.9651907170347154e-05,
 'epochs': 314.0}

In [ ]:
slim_train = SLIMMSERecommender(URM_train)
slim_train.fit(learning = best_hyperparams_slim["learning"], reg_1=best_hyperparams_slim["reg_1"], reg_2 = best_hyperparams_slim["reg_2"], epochs=int(best_hyperparams_slim["epochs"]))

result_df, _ = evaluator_validation.evaluateRecommender(slim_train)
result_df

Recommender_Base_Class: URM Detected 482 ( 3.8%) users with no interactions.
Recommender_Base_Class: URM Detected 340 ( 1.5%) items with no interactions.
Epoch 1 complete in in 5.94 seconds, loss is 9.938E-01. Samples per second 51582.53
Epoch 2 complete in in 2.03 seconds, loss is 9.817E-01. Samples per second 151198.45
Epoch 3 complete in in 0.94 seconds, loss is 9.699E-01. Samples per second 325460.85
Epoch 4 complete in in 1.87 seconds, loss is 9.587E-01. Samples per second 163871.91
Epoch 5 complete in in 1.80 seconds, loss is 9.479E-01. Samples per second 170414.77
Epoch 6 complete in in 1.64 seconds, loss is 9.370E-01. Samples per second 186617.64
Epoch 7 complete in in 1.53 seconds, loss is 9.268E-01. Samples per second 200336.61
Epoch 8 complete in in 1.46 seconds, loss is 9.166E-01. Samples per second 210470.43
Epoch 9 complete in in 1.35 seconds, loss is 9.069E-01. Samples per second 226940.60
Epoch 10 complete in in 1.25 seconds, loss is 8.974E-01. Samples per second 244206

PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.051345                 0.109071  0.099525  0.022688    0.047998   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.164905  0.090523  0.067742  0.371662      0.193078  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10          0.794113          0.295142    0.794113       0.015898   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10            8.298891                   0.991655             0.046242   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.639932                 3.048415      0.322301  

[1 rows x 27 columns]

In [ ]:
slim_hyp = SLIMMSERecommender(URM_train + URM_validation)
slim_hyp.fit(learning = best_hyperparams_slim["learning"], reg_1=best_hyperparams_slim["reg_1"], reg_2 = best_hyperparams_slim["reg_2"], epochs=int(best_hyperparams_slim["epochs"]))

result_df, _ = evaluator_test.evaluateRecommender(slim_hyp)
result_df

Recommender_Base_Class: URM Detected 217 ( 1.7%) users with no interactions.
Recommender_Base_Class: URM Detected 121 ( 0.5%) items with no interactions.
Epoch 1 complete in in 11.01 seconds, loss is 9.896E-01. Samples per second 34784.72
Epoch 2 complete in in 3.31 seconds, loss is 9.696E-01. Samples per second 115628.78
Epoch 3 complete in in 3.14 seconds, loss is 9.508E-01. Samples per second 121859.37
Epoch 4 complete in in 2.92 seconds, loss is 9.328E-01. Samples per second 131009.34
Epoch 5 complete in in 3.69 seconds, loss is 9.162E-01. Samples per second 103838.19
Epoch 6 complete in in 3.74 seconds, loss is 9.001E-01. Samples per second 102459.73
Epoch 7 complete in in 3.78 seconds, loss is 8.851E-01. Samples per second 101222.62
Epoch 8 complete in in 3.52 seconds, loss is 8.708E-01. Samples per second 108660.57
Epoch 9 complete in in 3.22 seconds, loss is 8.567E-01. Samples per second 118799.08
Epoch 10 complete in in 2.96 seconds, loss is 8.438E-01. Samples per second 12960

PRECISION PRECISION_RECALL_MIN_DEN   RECALL      MAP MAP_MIN_DEN  \
cutoff                                                                    
10      0.069919                 0.129377  0.11229  0.03394    0.061854   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.218763  0.115462  0.086178  0.446301      0.270742  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.369916     0.82885       0.020626   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10            8.793519                   0.994441             0.059252   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.677467                 2.585593      0.263595  

[1 rows x 27 columns]

In [ ]:
pickle.dump(slim_hyp, open("/content/drive/MyDrive/Prova/Training/Models/slim_hyp", "wb"))

In [ ]:
slim = SLIMMSERecommender(URM_train + URM_validation + URM_test)
slim.fit(learning = best_hyperparams_slim["learning"], reg_1=best_hyperparams_slim["reg_1"], reg_2 = best_hyperparams_slim["reg_2"], epochs=int(best_hyperparams_slim["epochs"]))

Epoch 1 complete in in 12.87 seconds, loss is 9.893E-01. Samples per second 37206.10
Epoch 2 complete in in 4.95 seconds, loss is 9.690E-01. Samples per second 96655.51
Epoch 3 complete in in 4.69 seconds, loss is 9.500E-01. Samples per second 102117.33
Epoch 4 complete in in 4.52 seconds, loss is 9.322E-01. Samples per second 105886.67
Epoch 5 complete in in 4.44 seconds, loss is 9.153E-01. Samples per second 107728.35
Epoch 6 complete in in 3.99 seconds, loss is 8.992E-01. Samples per second 120088.17
Epoch 7 complete in in 4.59 seconds, loss is 8.844E-01. Samples per second 104338.02
Epoch 8 complete in in 4.62 seconds, loss is 8.704E-01. Samples per second 103518.85
Epoch 9 complete in in 4.46 seconds, loss is 8.574E-01. Samples per second 107323.45
Epoch 10 complete in in 4.01 seconds, loss is 8.439E-01. Samples per second 119343.10
Epoch 11 complete in in 3.80 seconds, loss is 8.319E-01. Samples per second 126040.41
Epoch 12 complete in in 4.96 seconds, loss is 8.202E-01. Samples

In [ ]:
pickle.dump(slim, open("/content/drive/MyDrive/Prova/Training/Models/slim", "wb"))

# Neural Recommender (Not used in the application AI server)

In [ ]:
from Recommenders.Neural.MultVAERecommender import MultVAERecommender

RuntimeError: module compiled against API version 0x10 but this version of numpy is 0xf

RuntimeError: module compiled against API version 0x10 but this version of numpy is 0xf

RuntimeError: module compiled against API version 0x10 but this version of numpy is 0xf

SystemError: initialization of _pywrap_checkpoint_reader raised unreported exception

In [ ]:
class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["epochs"] = optuna_trial.user_attrs["epochs"]
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)ì


def objective_function_MultVAE(optuna_trial):

    # Earlystopping hyperparameters available in the framework
    full_hyperp = {"validation_every_n": 5,
                   "stop_on_validation": True,
                   "evaluator_object": evaluator_validation,
                   "lower_validations_allowed": 5,   # Higher values will result in a more "patient" earlystopping
                   "validation_metric": "MAP",

                   # MAX number of epochs (usually 500)
                   "epochs": 500,
                  }

    start_time = time.time()
    recommender_instance = MultVAERecommender(URM_train, force_gpu=True)
    recommender_instance.fit(learning_rate = optuna_trial.suggest_float("learning_rate", 1e-6, 1e-1, log=True),
                             l2_reg = optuna_trial.suggest_float("l2_reg", 1e-4, 1e-1, log=True),
                             dropout = optuna_trial.suggest_float("dropout", 0.1, 0.9, log=False),
                             batch_size = optuna_trial.suggest_categorical("batch_size", [1, 2, 4, 8, 16, 32, 64, 128, 256, 512, 1024]),
                             ** full_hyperp)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    epochs = recommender_instance.get_early_stopping_final_epochs_dict()["epochs"]
    optuna_trial.set_user_attr("epochs", epochs)
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_MultVAE,
                      callbacks=[save_results],
                      n_trials = 50)

In [ ]:
optuna_study.best_trial.params

In [ ]:
multvae = MultVAERecommender(URM_train + URM_validation, force_gpu=True)
multvae.fit(**optuna_study.best_trial.params)

result_df, _ = evaluator_test.evaluateRecommender(multvae)
result_df

#Hybrid Recommenders (Not used in the application AI server)

In [ ]:
from Recommenders.BaseRecommender import BaseRecommender

class ScoresHybridRecommender(BaseRecommender):
    """ ScoresHybridRecommender
    Hybrid of two prediction scores R = R1*alpha + R2*(1-alpha)

    """

    RECOMMENDER_NAME = "ScoresHybridRecommender"

    def __init__(self, URM_train, recommender_1, recommender_2):
        super(ScoresHybridRecommender, self).__init__(URM_train)

        self.URM_train = sps.csr_matrix(URM_train)
        self.recommender_1 = recommender_1
        self.recommender_2 = recommender_2


    def fit(self, alpha = 0.5):
        self.alpha = alpha


    def _compute_item_score(self, user_id_array, items_to_compute=None):

        # In a simple extension this could be a loop over a list of pretrained recommender objects
        item_weights_1 = self.recommender_1._compute_item_score(user_id_array)
        item_weights_2 = self.recommender_2._compute_item_score(user_id_array)

        item_weights = item_weights_1*self.alpha + item_weights_2*(1-self.alpha)

        return item_weights


In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_sim_hybrid(optuna_trial):

    start_time = time.time()
    recommender_instance = ScoresHybridRecommender(URM_train + URM_validation, ItemKNNCF, UserKNNCF)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_test.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_sim_hybrid,
                      callbacks=[save_results],
                      n_trials = 50)

In [ ]:
from Recommenders.BaseRecommender import BaseRecommender
from numpy import linalg as LA

class DifferentLossScoresHybridRecommender(BaseRecommender):
    """ ScoresHybridRecommender
    Hybrid of two prediction scores R = R1/norm*alpha + R2/norm*(1-alpha) where R1 and R2 come from
    algorithms trained on different loss functions.

    """

    RECOMMENDER_NAME = "DifferentLossScoresHybridRecommender"


    def __init__(self, URM_train, recommender_1, recommender_2):
        super(DifferentLossScoresHybridRecommender, self).__init__(URM_train)

        self.URM_train = sps.csr_matrix(URM_train)
        self.recommender_1 = recommender_1
        self.recommender_2 = recommender_2



    def fit(self, norm=1, alpha = 0.5):

        self.alpha = alpha
        self.norm = norm


    def _compute_item_score(self, user_id_array, items_to_compute=None):

        item_weights_1 = self.recommender_1._compute_item_score(user_id_array)
        item_weights_2 = self.recommender_2._compute_item_score(user_id_array)

        norm_item_weights_1 = LA.norm(item_weights_1, self.norm)
        norm_item_weights_2 = LA.norm(item_weights_2, self.norm)


        if norm_item_weights_1 == 0:
            raise ValueError("Norm {} of item weights for recommender 1 is zero. Avoiding division by zero".format(self.norm))

        if norm_item_weights_2 == 0:
            raise ValueError("Norm {} of item weights for recommender 2 is zero. Avoiding division by zero".format(self.norm))

        item_weights = item_weights_1 / norm_item_weights_1 * self.alpha + item_weights_2 / norm_item_weights_2 * (1-self.alpha)

        return item_weights

In [ ]:
slim_ials = DifferentLossScoresHybridRecommender(URM_train + URM_validation, slim_hyp, IALSRecommender_hyp)
slim_ials.fit(alpha = 0.717)

DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.


In [ ]:
#Current best hybrid rec-sys
p3beta_easer = DifferentLossScoresHybridRecommender(URM_train + URM_validation, P3Beta_hyp, easer_hyp)
p3beta_easer.fit(alpha = 0.7)

DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.


In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_final(optuna_trial):

    start_time = time.time()
    recommender_instance = DifferentLossScoresHybridRecommender(URM_train + URM_validation, elastic_net_hyp, p3beta_easer)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_test.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_final,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-10 08:41:41,015] A new study created in memory with name: no-name-3e1885b3-9a78-4866-ae3c-dfe0d023df80


DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
EvaluatorHoldout: Processed 10475 (100.0%) in 14.24 sec. Users per second: 736


[I 2024-01-10 08:41:55,279] Trial 0 finished with value: 0.05056221540326625 and parameters: {'alpha': 0.9736002075138753}. Best is trial 0 with value: 0.05056221540326625.


DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.


<ipython-input-86-65d96be83164>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-01-10 08:54:09,617] Trial 48 finished with value: 0.051235182028261356 and parameters: {'alpha': 0.6240677903588313}. Best is trial 21 with value: 0.051348895707846176.


DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.


<ipython-input-86-65d96be83164>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EvaluatorHoldout: Processed 10475 (100.0%) in 15.39 sec. Users per second: 681


[I 2024-01-10 08:54:25,034] Trial 49 finished with value: 0.05111328181232783 and parameters: {'alpha': 0.7132465661602462}. Best is trial 21 with value: 0.051348895707846176.
<ipython-input-86-65d96be83164>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'alpha': 0.5890074907627837}

In [ ]:
easer_hyp = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/easer_hyp", "rb"))

In [ ]:
easer = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/easer", "rb"))

In [ ]:
elastic_net_hyp = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/elastic_net_hyp", "rb"))

In [ ]:
elastic_net = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/elastic_net", "rb"))

In [ ]:
#Current best hybrid rec-sys
p3beta_easer = DifferentLossScoresHybridRecommender(URM_train + URM_validation + URM_test, P3Beta, easer)
p3beta_easer.fit(alpha = 0.7)
final = DifferentLossScoresHybridRecommender(URM_train + URM_validation + URM_test, elastic_net, p3beta_easer)
final.fit(alpha = 0.589)

In [ ]:
from Recommenders.BaseRecommender import BaseRecommender
from numpy import linalg as LA

class MultHybridRecommender(BaseRecommender):
    """ ScoresHybridRecommender
    Hybrid of two prediction scores R = R1/norm*alpha + R2/norm*(1-alpha) where R1 and R2 come from
    algorithms trained on different loss functions.

    """

    RECOMMENDER_NAME = "MultHybridRecommender"


    def __init__(self, URM_train, recommender_1, recommender_2, recommender_3):
        super(MultHybridRecommender, self).__init__(URM_train)

        self.URM_train = sps.csr_matrix(URM_train)
        self.recommender_1 = recommender_1
        self.recommender_2 = recommender_2
        self.recommender_3 = recommender_3



    def fit(self, norm=1, alpha = 0.5, beta = 0.5, gamma = 0.5):

        self.alpha = alpha
        self.beta = beta
        self.gamma = gamma
        self.norm = norm


    def _compute_item_score(self, user_id_array, items_to_compute=None):

        item_weights_1 = self.recommender_1._compute_item_score(user_id_array)
        item_weights_2 = self.recommender_2._compute_item_score(user_id_array)
        item_weights_3 = self.recommender_3._compute_item_score(user_id_array)

        norm_item_weights_1 = LA.norm(item_weights_1, self.norm)
        norm_item_weights_2 = LA.norm(item_weights_2, self.norm)
        norm_item_weights_3 = LA.norm(item_weights_3, self.norm)


        if norm_item_weights_1 == 0:
            raise ValueError("Norm {} of item weights for recommender 1 is zero. Avoiding division by zero".format(self.norm))

        if norm_item_weights_2 == 0:
            raise ValueError("Norm {} of item weights for recommender 2 is zero. Avoiding division by zero".format(self.norm))

        if norm_item_weights_3 == 0:
            raise ValueError("Norm {} of item weights for recommender 3 is zero. Avoiding division by zero".format(self.norm))

        item_weights = item_weights_1 / norm_item_weights_1 * self.alpha + item_weights_2 / norm_item_weights_2 * self.beta + item_weights_3 / norm_item_weights_3 * self.gamma

        return item_weights

In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_mult(optuna_trial):

    start_time = time.time()
    recommender_instance = MultHybridRecommender(URM_train, elastic_net_train, P3Beta_train, easer_train)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False),
                             beta = optuna_trial.suggest_float("beta", 0.01, 0.99, log=False),
                             gamma = optuna_trial.suggest_float("gamma", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_mult,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-10 08:56:18,297] A new study created in memory with name: no-name-9cce77d9-eff8-463b-a719-dae3afaf90df


MultHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
MultHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.
EvaluatorHoldout: Processed 10036 (100.0%) in 12.72 sec. Users per second: 789


[I 2024-01-10 08:56:31,038] Trial 0 finished with value: 0.031278255423333394 and parameters: {'alpha': 0.5817467580724521, 'beta': 0.3854581694424059, 'gamma': 0.5054951279986498}. Best is trial 0 with value: 0.031278255423333394.


MultHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
MultHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-98-09a07a98f278>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-01-10 09:07:39,923] Trial 48 finished with value: 0.03149890948142273 and parameters: {'alpha': 0.16865683017292776, 'beta': 0.38975376983353477, 'gamma': 0.04994031419010979}. Best is trial 37 with value: 0.031565938019953804.


MultHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
MultHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-98-09a07a98f278>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EvaluatorHoldout: Processed 10036 (100.0%) in 13.46 sec. Users per second: 746


[I 2024-01-10 09:07:53,424] Trial 49 finished with value: 0.030370815856567427 and parameters: {'alpha': 0.12194315551375243, 'beta': 0.17251774048768986, 'gamma': 0.8437921413871837}. Best is trial 37 with value: 0.031565938019953804.
<ipython-input-98-09a07a98f278>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'alpha': 0.1424127491787795,
 'beta': 0.23549056208241373,
 'gamma': 0.010639530347325479}

In [ ]:
final = MultHybridRecommender(URM_train + URM_validation, elastic_net_hyp, P3Beta_hyp, easer_hyp)
final.fit(alpha = 0.142, beta=0.235, gamma=0.010)


result_df, _ = evaluator_test.evaluateRecommender(final)
result_df

MultHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
MultHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
EvaluatorHoldout: Processed 10475 (100.0%) in 15.25 sec. Users per second: 687


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.098348                 0.168631  0.141884  0.051306     0.08601   

            MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                       ...   
10      0.28156  0.155095  0.116171  0.526014      0.375152  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.435987     0.82885       0.075383   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10           10.669025                   0.998639             0.216551   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.821959                 1.472852       0.29515  

[1 rows x 27 columns]

In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_final(optuna_trial):

    start_time = time.time()
    recommender_instance = DifferentLossScoresHybridRecommender(URM_train, elastic_net_train, P3Beta_train)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_final,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-10 09:11:22,656] A new study created in memory with name: no-name-12b5cb8d-fd26-45a1-a967-10e8b5dfeca5


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.
EvaluatorHoldout: Processed 10036 (100.0%) in 10.03 sec. Users per second: 1000


[I 2024-01-10 09:11:32,718] Trial 0 finished with value: 0.03152327810358932 and parameters: {'alpha': 0.34218743516512856}. Best is trial 0 with value: 0.03152327810358932.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-102-0aa0d610e67e>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-01-10 09:19:17,184] Trial 48 finished with value: 0.03156432082597907 and parameters: {'alpha': 0.4639309979522874}. Best is trial 17 with value: 0.031639016208317.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-102-0aa0d610e67e>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EvaluatorHoldout: Processed 10036 (100.0%) in 10.73 sec. Users per second: 935


[I 2024-01-10 09:19:27,948] Trial 49 finished with value: 0.03148651363029628 and parameters: {'alpha': 0.565598036680225}. Best is trial 17 with value: 0.031639016208317.
<ipython-input-102-0aa0d610e67e>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'alpha': 0.44238184898279254}

In [ ]:
final = DifferentLossScoresHybridRecommender(URM_train + URM_validation, elastic_net_hyp, P3Beta_hyp)
final.fit(alpha = 0.44)


result_df, _ = evaluator_test.evaluateRecommender(final)
result_df

DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
EvaluatorHoldout: Processed 10475 (100.0%) in 11.10 sec. Users per second: 944


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.098348                 0.168549  0.141826  0.051378    0.086068   

             MRR     NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                       ...   
10      0.282219  0.15521  0.116152  0.526492      0.375952  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.436382     0.82885       0.074542   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10           10.669641                   0.998664             0.214136   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.822006                 1.469676       0.29489  

[1 rows x 27 columns]

In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_final(optuna_trial):

    start_time = time.time()
    recommender_instance = DifferentLossScoresHybridRecommender(URM_train, easer_train, ItemKNNCF_train)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_final,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-10 10:22:31,042] A new study created in memory with name: no-name-f095c8f6-484b-432c-a6ab-8f71bdc66be3


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.
EvaluatorHoldout: Processed 10036 (100.0%) in 8.51 sec. Users per second: 1179


[I 2024-01-10 10:22:39,581] Trial 0 finished with value: 0.030504354957075423 and parameters: {'alpha': 0.1862715532896115}. Best is trial 0 with value: 0.030504354957075423.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-139-60ab243ebdf7>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-01-10 10:30:10,281] Trial 48 finished with value: 0.03061100277097715 and parameters: {'alpha': 0.45456000490300613}. Best is trial 22 with value: 0.030729338666515144.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-139-60ab243ebdf7>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EvaluatorHoldout: Processed 10036 (100.0%) in 8.51 sec. Users per second: 1179


[I 2024-01-10 10:30:18,821] Trial 49 finished with value: 0.02988926768395704 and parameters: {'alpha': 0.891059638018065}. Best is trial 22 with value: 0.030729338666515144.
<ipython-input-139-60ab243ebdf7>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'alpha': 0.3473293414676778}

In [ ]:
final = DifferentLossScoresHybridRecommender(URM_train + URM_validation, easer_hyp, ItemKNNCF_hyp)
final.fit(alpha = 0.34)


result_df, _ = evaluator_test.evaluateRecommender(final)
result_df

DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
EvaluatorHoldout: Processed 10475 (100.0%) in 11.84 sec. Users per second: 885


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.094539                 0.164152  0.138655  0.048384    0.081725   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.270499  0.148937  0.112424  0.518663      0.357209  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.429894     0.82885       0.053612   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10           10.158709                   0.998075             0.154009   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.782643                 1.676245      0.286825  

[1 rows x 27 columns]

In [ ]:
elastic_p3beta = DifferentLossScoresHybridRecommender(URM_train, elastic_net_train, P3Beta_train)
elastic_p3beta.fit(alpha = 0.44)
ease_item = DifferentLossScoresHybridRecommender(URM_train, easer_train, ItemKNNCF_train)
ease_item.fit(alpha = 0.34)

DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


In [ ]:
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_final(optuna_trial):

    start_time = time.time()
    recommender_instance = DifferentLossScoresHybridRecommender(URM_train, elastic_p3beta, ease_item)
    recommender_instance.fit(alpha = optuna_trial.suggest_float("alpha", 0.01, 0.99, log=False))

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_final,
                      callbacks=[save_results],
                      n_trials = 50)

[I 2024-01-10 10:31:26,624] A new study created in memory with name: no-name-d8f032a1-e1ec-417a-8b10-8b6c8674bd4d


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.
EvaluatorHoldout: Processed 10036 (100.0%) in 14.21 sec. Users per second: 706


[I 2024-01-10 10:31:40,858] Trial 0 finished with value: 0.031277947009812575 and parameters: {'alpha': 0.3485464158987349}. Best is trial 0 with value: 0.031277947009812575.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-143-372034ae2eb9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


...

[I 2024-01-10 10:44:06,144] Trial 48 finished with value: 0.031589243010875345 and parameters: {'alpha': 0.6707488297988153}. Best is trial 32 with value: 0.03166730721782554.


DifferentLossScoresHybridRecommender: URM Detected 482 ( 3.8%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 340 ( 1.5%) items with no interactions.


<ipython-input-143-372034ae2eb9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EvaluatorHoldout: Processed 10036 (100.0%) in 15.67 sec. Users per second: 641


[I 2024-01-10 10:44:21,844] Trial 49 finished with value: 0.03163651726799415 and parameters: {'alpha': 0.8289663027403388}. Best is trial 32 with value: 0.03166730721782554.
<ipython-input-143-372034ae2eb9>:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'alpha': 0.9367147642769019}

In [ ]:
elastic_p3beta = DifferentLossScoresHybridRecommender(URM_train + URM_validation, elastic_net_hyp, P3Beta_hyp)
elastic_p3beta.fit(alpha = 0.44)
ease_item = DifferentLossScoresHybridRecommender(URM_train + URM_validation, easer_hyp, ItemKNNCF_hyp)
ease_item.fit(alpha = 0.34)
final = DifferentLossScoresHybridRecommender(URM_train + URM_validation, elastic_p3beta, ease_item)
final.fit(alpha = 0.936)

result_df, _ = evaluator_test.evaluateRecommender(final)
result_df

DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 217 ( 1.7%) users with no interactions.
DifferentLossScoresHybridRecommender: URM Detected 121 ( 0.5%) items with no interactions.
EvaluatorHoldout: Processed 10475 (100.0%) in 16.36 sec. Users per second: 640


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10      0.098539                 0.169087  0.142303  0.051319    0.085971   

             MRR      NDCG        F1  HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                        ...   
10      0.281085  0.155168  0.116445  0.527255      0.374887  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10           0.82885          0.437015     0.82885       0.072897   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10           10.635933                   0.998635             0.209411   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                   0.81941                 1.480263      0.294337  

[1 rows x 27 columns]

In [ ]:
IALSRecommender_hyp = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/IALSRecommender_hyp", "rb"))
IALSRecommender = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/IALSRecommender", "rb"))
slim_hyp = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/slim_hyp", "rb"))
slim = pickle.load(open("/content/drive/MyDrive/Prova/Training/Models/slim", "rb"))

# Output creation

In [ ]:
#------------------------------------------------------------------------------------------------------------
                                        #Top Pop Recommended item function (default 10 item)
#------------------------------------------------------------------------------------------------------------

class TopPopRecommended(object):

    def fit(self, URM_train):

        item_popularity = np.ediff1d(URM_all.tocsc().indptr)

        # We are not interested in sorting the popularity value,
        # but to order the items according to it
        #self.popular_items = np.argsort(item_popularity)
        self.popular_items = np.argsort(item_popularity, kind="heapsort")
        self.popular_items = np.flip(self.popular_items, axis = 0)


    def recommend(self, at=10):

        recommended_items = self.popular_items[0:at]

        return recommended_items


In [ ]:
#------------------------------------------------------------------------------------------------------------
                                        #Funzione di Demap
#------------------------------------------------------------------------------------------------------------
def item_list_demap(item_list, mapping_items=item_original_ID_to_index):
  demapped_list=""

  for item in item_list:
    demapped_list = demapped_list + str(mapping_items.index[item])+ " "

  return demapped_list[0:-1];

In [ ]:
def print_output( recommendations, name="output" , mapping_users=user_original_ID_to_index, mapping_items = item_original_ID_to_index):
  check_list = []

  print("Avvio creazione del file "+'"' + name+ '"'+"...")

  with open('/content/drive/MyDrive/RSResources/input_files/data_target_users_test.csv', newline='') as csvfile:
    spamreader = csv.reader(csvfile, delimiter=' ', )
    next(spamreader)
    for row in spamreader:
        for user in row:
          check_list.append(user)

  #Computing the top recommendations...
  topPopRecommended= TopPopRecommended()
  topPopRecommended.fit(URM_train)
  top = item_list_demap(topPopRecommended.recommend())

  with open(name+".csv", 'w', newline='') as csvfile:
      spamwriter = csv.writer(csvfile, delimiter=",")
      spamwriter.writerow(["user_id","item_list"])
      count=0
      for user in check_list:
        try:
          #if mapping_users[np.int64(user)] in mapping_users.keys():
          spamwriter.writerow([user, item_list_demap(recommendations.recommend(mapping_users[np.int64(user)], 10), mapping_items)])
          count= count +1
        except:
          spamwriter.writerow([user, top])
          count= count +1
      """
      if(count != 18 ):
        print ("Errore il numero delle Righe è diverso da quello richesto")
        print (str(count)+"/10882")
        print ("ATTENZIONE stai provando a generare un file per il commit il valore di split è diverso da 1")
        if os.path.exists(name+".csv"):
            os.remove(name+".csv")
            print("File RIMOSSO")
        else:
            print("Il File Non esiste")
      elif (count == 18 ):
        print ("File Creato con successo")
      """

In [ ]:
URM_all = URM_train + URM_validation + URM_test

In [ ]:
best_recommender_hyperparams

{'similarity': 'euclidean',
 'topK': 702,
 'shrink': 221,
 'normalize': False,
 'normalize_avg_row': False,
 'similarity_from_distance_mode': 'log'}

In [ ]:
from Recommenders.KNN.ItemKNNCFRecommender import ItemKNNCFRecommender
ItemKNNCF = ItemKNNCFRecommender(URM_all)
ItemKNNCF.fit(**best_recommender_hyperparams)

Similarity column 58 (100.0%), 5902.17 column/sec. Elapsed time 0.01 sec


In [ ]:
print_output(ItemKNNCF, "output")

Avvio creazione del file "output"...
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui
Sono qui


# EASERRecommender

In [ ]:
from Recommenders.EASE_R.EASE_R_Recommender import EASE_R_Recommender
import time

class SaveResults(object):

    def __init__(self):
        self.results_df = pd.DataFrame(columns=["result", "train_time (min)"])

    def __call__(self, optuna_study, optuna_trial):
        hyperparam_dict = optuna_trial.params.copy()
        hyperparam_dict["result"] = optuna_trial.values[0]

        # Retrieve the optimal number of epochs and training time from the "user attributes" of the trial
        hyperparam_dict["train_time (min)"] = optuna_trial.user_attrs["train_time (min)"]

        self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


def objective_function_ease(optuna_trial):

    start_time = time.time()
    recommender_instance = EASE_R_Recommender(URM_train)
    recommender_instance.fit(l2_norm = optuna_trial.suggest_float("l2_norm", 1e1, 1e3, log=True),
                             topK = optuna_trial.suggest_int("topK", 5, 1000),
                             normalize_matrix=False)

    # Add the number of epochs selected by earlystopping as a "user attribute" of the optuna trial
    optuna_trial.set_user_attr("train_time (min)", (time.time() - start_time)/60)

    result_df, _ = evaluator_validation.evaluateRecommender(recommender_instance)

    return result_df.loc[10]["MAP"]

In [ ]:
optuna_study = optuna.create_study(direction="maximize")

save_results = SaveResults()

optuna_study.optimize(objective_function_ease,
                      callbacks=[save_results],
                      n_trials = 20)

[I 2024-09-02 10:17:32,619] A new study created in memory with name: no-name-d457c540-fa8c-439d-89ac-2575f4e4a9e7


EASE_R_Recommender: URM Detected 1 (12.5%) users with no interactions.
EASE_R_Recommender: URM Detected 16 (27.6%) items with no interactions.
EASE_R_Recommender: Fitting model... 
EASE_R_Recommender: Fitting model... done in 0.01 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 811


[I 2024-09-02 10:17:32,660] Trial 0 finished with value: 0.0 and parameters: {'l2_norm': 418.90690537838054, 'topK': 579}. Best is trial 0 with value: 0.0.


EASE_R_Recommender: URM Detected 1 (12.5%) users with no interactions.
EASE_R_Recommender: URM Detected 16 (27.6%) items with no interactions.
EASE_R_Recommender: Fitting model... 
EASE_R_Recommender: Fitting model... done in 0.00 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 811


<ipython-input-37-6fe6c5899cb0>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)
[I 2024-09-02 10:17:32,725] Trial 1 finished with value: 0.0 and parameters: {'l2_norm': 854.3450618716261, 'topK': 355}. Best is trial 0 with value: 0.0.


...

[I 2024-09-02 10:17:34,062] Trial 17 finished with value: 0.0 and parameters: {'l2_norm': 35.7634698221219, 'topK': 235}. Best is trial 0 with value: 0.0.


EASE_R_Recommender: URM Detected 1 (12.5%) users with no interactions.
EASE_R_Recommender: URM Detected 16 (27.6%) items with no interactions.
EASE_R_Recommender: Fitting model... 
EASE_R_Recommender: Fitting model... done in 0.01 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 846


<ipython-input-37-6fe6c5899cb0>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)
[I 2024-09-02 10:17:34,149] Trial 18 finished with value: 0.0 and parameters: {'l2_norm': 662.8219815732566, 'topK': 490}. Best is trial 0 with value: 0.0.
<ipython-input-37-6fe6c5899cb0>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


EASE_R_Recommender: URM Detected 1 (12.5%) users with no interactions.
EASE_R_Recommender: URM Detected 16 (27.6%) items with no interactions.
EASE_R_Recommender: Fitting model... 
EASE_R_Recommender: Fitting model... done in 0.00 sec
EvaluatorHoldout: Processed 5 (100.0%) in 0.01 sec. Users per second: 486


[I 2024-09-02 10:17:34,243] Trial 19 finished with value: 0.0 and parameters: {'l2_norm': 346.63327729878256, 'topK': 808}. Best is trial 0 with value: 0.0.
<ipython-input-37-6fe6c5899cb0>:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  self.results_df = self.results_df.append(hyperparam_dict, ignore_index=True)


In [ ]:
optuna_study.best_trial.params

{'l2_norm': 418.90690537838054, 'topK': 579}

In [ ]:
easer_hyp = EASE_R_Recommender(URM_train + URM_validation)
easer_hyp.fit(**optuna_study.best_trial.params)

result_df, _ = evaluator_test.evaluateRecommender(easer_hyp)
result_df

EASE_R_Recommender: URM Detected 8 (13.8%) items with no interactions.
EASE_R_Recommender: Fitting model... 
EASE_R_Recommender: Fitting model... done in 0.00 sec
EvaluatorHoldout: Processed 6 (100.0%) in 0.01 sec. Users per second: 880


PRECISION PRECISION_RECALL_MIN_DEN    RECALL       MAP MAP_MIN_DEN  \
cutoff                                                                      
10          0.05                 0.263889  0.263889  0.021825    0.089286   

             MRR      NDCG        F1 HIT_RATE ARHR_ALL_HITS  ...  \
cutoff                                                       ...   
10      0.218254  0.159269  0.084071      0.5      0.218254  ...   

       COVERAGE_USER COVERAGE_USER_HIT USERS_IN_GT DIVERSITY_GINI  \
cutoff                                                              
10              0.75             0.375        0.75       0.472316   

       SHANNON_ENTROPY RATIO_DIVERSITY_HERFINDAHL RATIO_DIVERSITY_GINI  \
cutoff                                                                   
10            4.989898                   0.988128             0.638567   

       RATIO_SHANNON_ENTROPY RATIO_AVERAGE_POPULARITY RATIO_NOVELTY  
cutoff                                                               
10                  0.897834                 0.889064      1.334274  

[1 rows x 27 columns]